In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import librosa
import librosa.display
import sklearn as skl
import sklearn.utils
import IPython.display as ipd
from sklearn.model_selection import train_test_split
import ast

In [2]:
file_paths = pd.read_csv('data/all_data_paths.txt', header = None, names = ['file_path'])

train_paths, test_paths = train_test_split(file_paths, test_size=0.33)

file_paths.head()

file_path
0  000/000002.mp3
1  000/000005.mp3
2  000/000010.mp3
3  000/000140.mp3
4  000/000141.mp3

In [3]:
music_data = pd.read_csv('data/fma_metadata/tracks.csv', skiprows = [0,1,2], 
                         usecols = [0, 6, 8, 11, 26, 39, 41, 44, 47, 52], 
                         names = ['track_id', 'album_id', 'album_listens', 'album_title', 'artist_name',
                                 'track_favorites', 'track_genres', 'track_interest', 'track_listens', 'track_title'])

music_data['track_genres'] = music_data['track_genres'].apply(ast.literal_eval)

music_data.head()

track_id  album_id  album_listens           album_title artist_name  \
0         2         1           6073  AWOL - A Way Of Life        AWOL   
1         3         1           6073  AWOL - A Way Of Life        AWOL   
2         5         1           6073  AWOL - A Way Of Life        AWOL   
3        10         6          47632     Constant Hitmaker   Kurt Vile   
4        20         4           2710                 Niris  Nicky Cook   

   track_favorites track_genres  track_interest  track_listens  \
0                2         [21]            4656           1293   
1                1         [21]            1470            514   
2                6         [21]            1933           1151   
3              178         [10]           54881          50135   
4                0    [76, 103]             978            361   

       track_title  
0             Food  
1     Electric Ave  
2       This World  
3          Freeway  
4  Spiritual Level

In [4]:
genre_df = pd.read_csv('data/fma_metadata/genres.csv', usecols=[0, 3])
genre_df

genre_id          title
0           1    Avant-Garde
1           2  International
2           3          Blues
3           4           Jazz
4           5      Classical
..        ...            ...
158      1032        Turkish
159      1060          Tango
160      1156           Fado
161      1193      Christmas
162      1235   Instrumental

[163 rows x 2 columns]

In [5]:
index = 1999
filename = 'data/fma_small/' + file_paths['file_path'][index]

y, sr = librosa.load(filename, sr=None, mono=True)
print('Duration: {:.2f}s, {} samples'.format(y.shape[-1] / sr, y.size))

start, end = 7, 17
# ipd.Audio(data=x[start*sr:end*sr], rate=sr)
ipd.Audio(data = y, rate = sr)

/root/miniconda3/lib/python3.9/site-packages/librosa/core/audio.py:165: UserWarning: PySoundFile failed. Trying audioread instead.
  warnings.warn("PySoundFile failed. Trying audioread instead.")


Duration: 29.98s, 1321967 samples


In [6]:
file_paths['file_path'][index]

'049/049062.mp3'

In [7]:
song_id = file_paths['file_path'][index].rsplit('/')[1].rsplit('.')[0].lstrip('0')
associated_genres_numeric = music_data[music_data['track_id'] == int(song_id)]['track_genres'].item()
associated_genres = [genre_df[genre_df['genre_id'] == num]['title'].item() for num in associated_genres_numeric]

In [8]:
import SpectrogramDataset
import data_generation

In [9]:
file_paths = pd.read_csv('data/all_data_paths.txt', header = None, names = ['file_path'])
music_data = pd.read_csv('data/fma_metadata/tracks.csv', skiprows = [0,1,2], 
                         usecols = [0, 6, 8, 11, 26, 39, 41, 44, 47, 52], 
                         names = ['track_id', 'album_id', 'album_listens', 'album_title', 'artist_name',
                                 'track_favorites', 'track_genres', 'track_interest', 'track_listens', 'track_title'])

music_data['track_genres'] = music_data['track_genres'].apply(ast.literal_eval)

In [10]:
file_path_df, track_df, genre_df = SpectrogramDataset.create_dataframes("data/all_data_paths.txt", "data/fma_metadata/tracks.csv","data/fma_metadata/genres.csv")


In [11]:
print(file_path_df.head())
print(track_df.head())
print(genre_df.head())

        file_path
0  000/000002.mp3
1  000/000005.mp3
2  000/000010.mp3
3  000/000140.mp3
4  000/000141.mp3
   track_id  album_id  album_listens           album_title artist_name  \
0         2         1           6073  AWOL - A Way Of Life        AWOL   
1         3         1           6073  AWOL - A Way Of Life        AWOL   
2         5         1           6073  AWOL - A Way Of Life        AWOL   
3        10         6          47632     Constant Hitmaker   Kurt Vile   
4        20         4           2710                 Niris  Nicky Cook   

   track_favorites track_genres  track_interest  track_listens  \
0                2         [21]            4656           1293   
1                1         [21]            1470            514   
2                6         [21]            1933           1151   
3              178         [10]           54881          50135   
4                0    [76, 103]             978            361   

       track_title  
0             Food  
1     El

In [ ]:
train_data, validation_data, test_data = SpectrogramDataset.create_dataset(file_paths, track_df, genre_df)


In [14]:
genres = []
for i in range(len(train_data)):
    genre = train_data[i][1]
    if genre not in genres:
        genres.append(genre)
        
print(genres)


[]


In [8]:
len(genres)

0

In [ ]:
import torch
import torch.nn as nn
import torch.nn.functional as F
import torchvision
import torchvision.transforms as transforms


In [18]:

import torch.nn as nn
import torch.nn.functional as F
#device = torch.device("cuda:0")


#part c
class Net(nn.Module):
    def __init__(self):
        super(Net, self).__init__()
        self.conv1 = nn.Conv2d(1, 3, 5)
        self.fc1 = nn.Linear(29946, 512)
        self.fc2 = nn.Linear(512, 256)
        self.fc3 = nn.Linear(256, 103)

    def forward(self, x):
        x = F.max_pool2d(F.relu(self.conv1(x)), (4, 8))
        x = x.view(-1, 29946)
        x = F.relu(self.fc1(x))
        x = F.relu(self.fc2(x))
        x = self.fc3(x)

        return x

model = Net()
#model.to(device)

In [19]:
import torch.optim as optim
learning_rate = 1e-4
criterion = nn.CrossEntropyLoss(reduction='sum')
optimizer = torch.optim.Adam(model.parameters(), lr=learning_rate)
#optimizer = optim.SGD(model.parameters(), lr=learning_rate, momentum=0.80) 


In [20]:
def genre(strgenre):
    label = torch.LongTensor(1) 
    label[0] = genres.index(strgenre)
    return label

In [21]:
acc_train1 = ()
acc_val1 = ()

for epoch in range(10):  # loop over the dataset multiple times
    running_loss = 0.0
#     for i, data in enumerate(train_data, 0):
        # get the inputs; data is a list of [inputs, labels]
        #inputs, labels = data[0].to(device), data[1].to(device)
        
        inputs, labels = data[0], genre(data[1])
        
        inputs = inputs.unsqueeze(0).unsqueeze(0)
        # zero the parameter gradients
        
        optimizer.zero_grad()
       

        # forward + backward + optimize
        outputs = model(inputs)
        
        loss = criterion(outputs, labels)
        
        loss.backward()
      
        optimizer.step()
        
        
        # print statistics
        running_loss += loss.item()
    #save model
    torch.save(model, 'model.pt')
    print(epoch, running_loss)

print('Finished Training')

0 5.760734558105469
0 2.8803672790527344
0 28.82830047607422
0 55.93823432922363
0 52.8399772644043
0 47.99799315134684
0 42.17379406520298
0 45.368343114852905
0 40.66050545374552
0 38.96091361045838
0 35.77023373950612
0 33.40239848693212
0 31.311630194003765
0 29.431475860731943
0 30.374864276250204
0 30.112750247120857
0 29.027833391638364
0 27.816420038541157
0 31.4398709472857
0 31.999452793598174
0 30.475671041548637
0 30.004887494144484
0 32.663165050976005
0 31.52872127291842
0 30.521111946080055
0 32.512131800993444
0 32.1707732235704
0 32.09517993243493
0 31.983842882594438
0 33.95506931938556
0 33.94147476071145
0 33.62969294188383
0 34.051927768803246
0 33.54449173981501
0 32.70597771234024
0 33.412422365594466
0 32.681917886458756
0 32.259909805481584
0 31.51795614681051
0 30.935917592032457
0 30.40052076663787
0 30.057864484317438
0 29.40652446412643
0 28.76105631750976
0 29.509063914072694
0 28.950024332675124
0 28.647478567779235
0 29.08690549680235
0 29.41702334490252

0 13.72980561504239
0 13.740412080328438
0 13.753624207783156
0 13.736642148688462
0 13.731513829153728
0 13.715057111589953
0 13.681379370839144
0 13.656346356632453
0 13.629390330533608
0 13.596148058140232
0 13.575034424503599
0 13.594153012921753
0 13.590329398709649
0 13.56835910766506
0 13.585369064025661
0 13.552722303713573
0 13.595676610596577
0 13.63319082673754
0 13.609628386970751
0 13.58337217095449
0 13.559334629591005
0 13.541470694119164
0 13.516227675189759
0 13.494968467530047
0 13.472367138386728
0 13.471997827236475
0 13.447036612313973
0 13.424582217147252
0 13.40143867064284
0 13.380849346810553
0 13.354019644449428
0 13.331128408871152
0 13.312070735691162
0 13.290162808692786
0 13.270616280704642
0 13.275471618772483
0 13.255954462358936
0 13.23466880825105
0 13.21490457370325
0 13.194223779251198
0 13.1690292059168
0 13.149735042224481
0 13.130125675810488
0 13.108081284219995
0 13.08416783924944
0 13.066637329804898
0 13.039160751870655
0 13.021937459654948
0 

0 9.721530097828754
0 9.714210833013379
0 9.707735618853755
0 9.702236570532511
0 9.695607370510276
0 9.687232110620235
0 9.680137600660569
0 9.673817755816987
0 9.66541185897023
0 9.66365817696993
0 9.658172422678332
0 9.656066622997132
0 9.650236640761882
0 9.65409703517307
0 9.645159783572714
0 9.643421578072282
0 9.645274884664202
0 9.636837678368506
0 9.632918071442194
0 9.626720581984731
0 9.619829145976633
0 9.610215286928272
0 9.603036517602344
0 9.596684133978929
0 9.589008242428543
0 9.581490679323263
0 9.601987134127244
0 9.593268835805443
0 9.586907123844068
0 9.604891018601416
0 9.596387493137804
0 9.589748389412444
0 9.586766177603495
0 9.58321416216447
0 9.58011473393121
0 9.573515424858261
0 9.568936924003193
0 9.561362520584447
0 9.557589610566055
0 9.549927557141286
0 9.545154024548426
0 9.5449464995441
0 9.539236088222344
0 9.532058659497764
0 9.526234045654345
0 9.519249590149949
0 9.512867096990792
0 9.504793593524571
0 9.496292143738165
0 9.489106295346042
0 9.486

0 8.113405035403684
0 8.109959093539391
0 8.105686411225474
0 8.105348627416424
0 8.101507389306828
0 8.095386091333756
0 8.091236529956173
0 8.086233913339042
0 8.082682071048971
0 8.085325806823096
0 8.083907162575384
0 8.077511594088342
0 8.07573807040747
0 8.072710905666856
0 8.068082890067616
0 8.064341058253662
0 8.057875178398396
0 8.053862914226238
0 8.050566544079686
0 8.047473954682406
0 8.041347170753642
0 8.040518442677952
0 8.037440269729032
0 8.035091466817741
0 8.030953774762096
0 8.027908387152086
0 8.025239641927849
0 8.020649883285788
0 8.017229774152037
0 8.015080948655335
0 8.013648224670982
0 8.00925094992553
0 8.005112362395296
0 8.001462361670114
0 7.997305898024692
0 7.9939634150120025
0 7.9906056351127015
0 7.989220597100031
0 7.986482392982279
0 7.98352632586231
0 7.9805286004137415
0 7.9782272972918475
0 7.977014130264545
0 7.973318699570498
0 7.970240963300007
0 7.967618231681373
0 7.9652317041744825
0 7.962198946814183
0 7.959147896738958
0 7.95486245180814

0 7.157261843494528
0 7.15487084829641
0 7.152772565496638
0 7.151095026869346
0 7.147016449734341
0 7.143667215180898
0 7.142060963698284
0 7.138722724122294
0 7.136796050727641
0 7.133143727398564
0 7.131426634570842
0 7.128552399269492
0 7.126590263493918
0 7.124896742052287
0 7.123532989680097
0 7.121343948203518
0 7.119641208886902
0 7.1179454746170485
0 7.114762040383703
0 7.114803602053649
0 7.112666109338918
0 7.111659498885708
0 7.11001500595903
0 7.107766217042925
0 7.105222136289748
0 7.1012263246889455
0 7.09927790453335
0 7.095159451133478
0 7.092393516093997
0 7.090253724230592
0 7.0881493026580245
0 7.08630044112272
0 7.083766159814446
0 7.0820736506023465
0 7.080176113999275
0 7.087059639647693
0 7.08946176617262
0 7.0854015554834575
0 7.083684811551145
0 7.080801920624035
0 7.0814960692718305
0 7.0798775547126995
0 7.078878210361903
0 7.076913882370433
0 7.0748872577244315
0 7.071869732358497
0 7.069218946840319
0 7.067178273242759
0 7.065803207650755
0 7.0624151568579

...

9 0.15144996150129175
9 0.1514169370875322
9 0.15138439467607356
9 0.15135266943786538
9 0.1513196878145405
9 0.1512867395985873
9 0.15125382476651475
9 0.1512208862158252
9 0.15118796203402537
9 0.1511550523674254
9 0.1511222097352195
9 0.1510893284885408
9 0.15105646940463283
9 0.15102362085428156
9 0.15099318864696262
9 0.15096038293199499
9 0.15092760559623705
9 0.15089485268370825
9 0.15086207086022912
9 0.15082930721296492
9 0.1507965538346342
9 0.15076397746248313
9 0.15073149358873153
9 0.1506987827611298
9 0.15066608692965228
9 0.15063362029527563
9 0.150600951975975
9 0.15056829790087783
9 0.15053565790566845
9 0.1505082061248123
9 0.15047559329574953
9 0.15045109434739085
9 0.15042248423358934
9 0.15038995064531446
9 0.15035781411975205
9 0.15032592042844486
9 0.15029338939177997
9 0.15026210844407253
9 0.15022961595931872
9 0.15019712688130185
9 0.15016465182684102
9 0.1501322194920612
9 0.15009979630723805
9 0.15006736341210422
9 0.1500351052699338
9 0.15000270027959473
9 

9 0.1436306516831654
9 0.14360172440501426
9 0.1435732236606518
9 0.14354449235324926
9 0.14351700873315462
9 0.14348812044637257
9 0.14345939724431825
9 0.14343053692357713
9 0.14340610802325307
9 0.14338011004775025
9 0.1433512783344891
9 0.1433225729329887
9 0.14329399678917615
9 0.14326524077404165
9 0.14323729236713803
9 0.14320868816046506
9 0.14318551989661063
9 0.14315710325269765
9 0.1431283687682699
9 0.1430996396697616
9 0.14307110601111214
9 0.14304240282455702
9 0.1430373167035509
9 0.1430086296794808
9 0.14298292613577895
9 0.14295426075363465
9 0.14292566876381993
9 0.14289704108459372
9 0.14286841014067775
9 0.1428398914160335
9 0.1428126849875336
9 0.14293562469639504
9 0.14290711629882233
9 0.14288208782602077
9 0.14285349425231134
9 0.14282500664522016
9 0.14279643592974803
9 0.14276787740550007
9 0.14273933585632148
9 0.14320184920725954
9 0.14317322601133564
9 0.143144614255538
9 0.14311601393300943
9 0.14308742506071145
9 0.14305901657699083
9 0.14303045047943153


9 0.13779954974764552
9 0.13777376872804822
9 0.13774982991455695
9 0.13772406783677227
9 0.13770059946397648
9 0.13767530802052833
9 0.13764957431809458
9 0.1376244228347192
9 0.13760420686672867
9 0.1375785008688085
9 0.13755282451126954
9 0.13752713770930666
9 0.13750165792690863
9 0.13747599026629134
9 0.13745051882789347
9 0.1374251416993743
9 0.13740322538801641
9 0.13737759621804946
9 0.1374056185702727
9 0.13764023874816783
9 0.13761457877062516
9 0.13758892833655795
9 0.13756328746284632
9 0.13753765614414631
9 0.1375120355298989
9 0.1374864233049911
9 0.1374608219288307
9 0.13743590392089416
9 0.13741213948980746
9 0.1373865713585228
9 0.13736100630988893
9 0.13733545077383127
9 0.13730995039641886
9 0.13731099977740735
9 0.13728546790612972
9 0.13726122832556908
9 0.13723571508610335
9 0.13721021152873428
9 0.1371847172493718
9 0.13716381010005016
9 0.13714239294087063
9 0.13711692545843035
9 0.1371362208406371
9 0.13711077639522018
9 0.13708532896084838
9 0.1370598920103677

9 0.13343125272447226
9 0.13340793795629827
9 0.1333846311886609
9 0.13336200151781558
9 0.13333871091328922
9 0.13331543468685886
9 0.13329263582568354
9 0.13326936952513793
9 0.13324611134546513
9 0.13322286128241412
9 0.13319968867646179
9 0.13317645482181736
9 0.1335502856928986
9 0.13352701539451925
9 0.13350424713119882
9 0.1334809763891505
9 0.13345771392440403
9 0.13343704768836268
9 0.13341380081594312
9 0.13421963351822827
9 0.13419810225522613
9 0.13417618120900185
9 0.1341528715232626
9 0.13413264918156664
9 0.1341099736678346
9 0.13408667039564326
9 0.13406371309791837
9 0.13404039460929976
9 0.13401739476716726
9 0.13399409144691563
9 0.13397079670601905
9 0.13394750958682802
9 0.13392423056187375
9 0.1339009596476509
9 0.1338779401000012
9 0.13385468529018707
9 0.1338314390339383
9 0.13380822235625353
9 0.13378505992152726
9 0.13376183855978185
9 0.13373866224572323
9 0.13371547289985852
9 0.13369292433861452
9 0.13366973389206835
9 0.1336465515307306
9 0.133623394158388

9 0.1312695260173737
9 0.1312480592672499
9 0.13122823098256214
9 0.13137614940298412
9 0.13135472608119447
9 0.1313335483379239
9 0.13131328223301225
9 0.13129179087305318
9 0.13127030637119208
9 0.13124905896461783
9 0.13122758848220908
9 0.13120623308304985
9 0.13118477662629055
9 0.1311633271860312
9 0.13114803009076306
9 0.13112660343041338
9 0.13110517401328145
9 0.13108375159922697
9 0.13106350132671984
9 0.1310420927182052
9 0.13102071522297282
9 0.13099934827098458
9 0.13097843001103163
9 0.13096212344631739
9 0.130940748854601
9 0.1309193812583795
9 0.1309011215794304
9 0.13087976771087695
9 0.13085848985744497
9 0.1308517850977075
9 0.13083044940798016
9 0.13080913118834156
9 0.13078780940656676
9 0.13076649457452527
9 0.1307499952348988
9 0.13072878278441047
9 0.13070748798350082
9 0.1306862001190084
9 0.13066491990578824
9 0.1306474896710562
9 0.13062622196966095
9 0.13060496155999368
9 0.13058370770131833
9 0.13056246075896538
9 0.13054122076834548
9 0.13051998764850678
9

In [29]:

#Testing Accuracy
model.eval()
correct = 0
total = 0
with torch.no_grad():
    for i, data in enumerate(test_data, 0):
        #valinputs, labels = data[0].to(device), data[1].to(device)
        inputs, labels = data[0], genre(data[1])
        inputs = inputs.unsqueeze(0).unsqueeze(0)
        #print(inputs.shape)

        outputs = model(inputs)
        _, predicted = torch.max(outputs.data, 1)
        total += labels.size(0)
        correct += (predicted == labels).sum().item()
acc_val1 = np.append(acc_val1, correct / total)
print('Accuracy of the network on the test set: %.2f %%' % (100 * correct / total))


Accuracy of the network on the test set: 17.27 %
